# 손동작 분류 - catboost
- https://dacon.io/competitions/official/235876/overview/description
- https://www.dacon.io/codeshare/2750 :catboost
- https://catboost.ai/en/docs/concepts/python-reference_catboostclassifier_grid_search : catboost 공식

In [2]:
import torch
import matplotlib.pyplot as plt
import numpy as np
import torch
import torch.nn as nn # 인공 신경망 모델들 모아놓은 모듈
import torch.nn.functional as F #그중 자주 쓰이는것들을 F로
from torchvision import transforms, datasets
import cv2
import pandas as pd
import os
from glob import glob
import torchvision.models as models
import sys
import librosa, librosa.display 

from pytorchtools.pytorchtools import EarlyStopping # 현재 폴더에 추가된 모듈.


if torch.cuda.is_available():
    DEVICE = torch.device('cuda')
else:
    DEVICE = torch.device('cpu')
#DEVICE = torch.device('cpu')
print('Using Pytorch version : ',torch.__version__,' Device : ',DEVICE)

Using Pytorch version :  1.9.0  Device :  cuda


In [3]:
train=pd.read_csv("./data/train_std.csv")
train.head()

sensor_1  sensor_2  sensor_3  sensor_4  sensor_5  sensor_6  sensor_7  \
0 -0.535371 -0.125639  0.341578 -0.451265 -0.258112  0.024504 -0.035601   
1 -0.194913 -0.135612  0.192241 -0.699634 -0.070194 -0.409077  1.003842   
2  1.661792 -0.282778  0.035701 -1.403838  0.795608  2.440908 -0.784159   
3 -0.192544 -0.260938  0.825381 -0.197252 -0.020994  0.408111 -1.082022   
4  0.344222  0.400669 -1.359199  0.057862  2.349527  1.504501 -0.817374   

   sensor_8  sensor_9  sensor_10  ...  sensor_24  sensor_25  sensor_26  \
0 -0.062341  0.495730   0.561387  ...  -0.425023  -0.499626  -0.807129   
1 -0.570637 -0.496736  -0.549809  ...  -0.120779  -0.659965  -0.421554   
2 -1.021484 -0.750397  -0.809140  ...  -0.416751   4.496282  -0.821026   
3  0.012872 -0.086870   0.284354  ...  -0.128610  -0.086139   0.292807   
4 -0.766131 -1.742301  -0.541734  ...  -0.124109   0.908166   0.256060   

   sensor_27  sensor_28  sensor_29  sensor_30  sensor_31  sensor_32  target  
0   0.271689   1.408115  -0.263322  -0.702508  -0.238269  -0.735616       1  
1   0.338467   0.704214   0.847177  -0.129756  -0.155609  -0.974972       1  
2   0.468867   0.392232  -3.454223  -0.529888  -0.319460  -0.316562       0  
3   0.387015  -0.065044  -0.336256  -0.398988  -0.513363  -0.184111       1  
4  -0.501660   1.104734   0.180913   0.531208   0.469003  -1.661853       2  

[5 rows x 33 columns]

In [4]:
test=pd.read_csv("./data/test_std.csv")
test.head()

id  sensor_1  sensor_2  sensor_3  sensor_4  sensor_5  sensor_6  sensor_7  \
0   1  0.005674  0.676368 -0.115694 -0.842619 -0.162445 -1.488116  0.071972   
1   2  0.582327 -1.611717  0.970755  2.533359 -0.398683  0.801910  0.307658   
2   3 -0.406466  0.129206 -0.073880 -0.401250 -0.330870  0.132228  0.503219   
3   4  0.001535 -0.535835  0.468239  1.493656 -0.177808 -0.812185  0.084399   
4   5 -0.662690 -0.285824  0.307139 -0.582444  2.353133 -0.679244 -0.424087   

   sensor_8  sensor_9  ...  sensor_23  sensor_24  sensor_25  sensor_26  \
0  1.374886  0.669053  ...   0.312165   0.385398   0.158167  -0.534629   
1  0.256059  0.337094  ...  -0.304989  -1.779163  -1.418008  -1.520688   
2 -0.590254  0.501513  ...  -0.034375  -0.524039  -0.002156   0.405970   
3  0.068180  0.090225  ...  -0.387284   0.185620   0.075617   0.702048   
4 -0.981423 -4.787554  ...  -0.076846  -1.571478  -0.564297   0.113274   

   sensor_27  sensor_28  sensor_29  sensor_30  sensor_31  sensor_32  
0   0.035820   0.331942  -0.658255   0.549249  -0.077809   0.708034  
1   0.007826   0.454621   0.654006  -0.387429   2.187045   3.454621  
2   0.190804  -0.719914  -0.401736  -0.939436   0.110953  -0.200973  
3   1.574165  -0.077081  -0.100479   0.005149  -0.974656  -0.466246  
4   0.459036   0.206241   3.876766   0.407601  -0.697985  -0.448883  

[5 rows x 33 columns]

In [5]:
train

sensor_1  sensor_2  sensor_3  sensor_4  sensor_5  sensor_6  sensor_7  \
0    -0.535371 -0.125639  0.341578 -0.451265 -0.258112  0.024504 -0.035601   
1    -0.194913 -0.135612  0.192241 -0.699634 -0.070194 -0.409077  1.003842   
2     1.661792 -0.282778  0.035701 -1.403838  0.795608  2.440908 -0.784159   
3    -0.192544 -0.260938  0.825381 -0.197252 -0.020994  0.408111 -1.082022   
4     0.344222  0.400669 -1.359199  0.057862  2.349527  1.504501 -0.817374   
...        ...       ...       ...       ...       ...       ...       ...   
2330 -0.345718  5.393804  0.604643 -1.226100  0.703314 -9.695606 -1.486334   
2331 -0.262199 -0.548707 -0.039446  0.268665 -0.174773 -0.395801 -0.102970   
2332 -0.783697  0.808895 -0.307187 -0.701039  0.445133  1.112023  1.223604   
2333 -0.347194  0.406962 -0.450592 -0.245049  1.472717 -0.704114  0.341756   
2334 -0.160036 -0.949139 -1.729971  1.287781  0.354088  1.102235  0.710240   

      sensor_8  sensor_9  sensor_10  ...  sensor_24  sensor_25  sensor_26  \
0    -0.062341  0.495730   0.561387  ...  -0.425023  -0.499626  -0.807129   
1    -0.570637 -0.496736  -0.549809  ...  -0.120779  -0.659965  -0.421554   
2    -1.021484 -0.750397  -0.809140  ...  -0.416751   4.496282  -0.821026   
3     0.012872 -0.086870   0.284354  ...  -0.128610  -0.086139   0.292807   
4    -0.766131 -1.742301  -0.541734  ...  -0.124109   0.908166   0.256060   
...        ...       ...        ...  ...        ...        ...        ...   
2330  0.822807 -1.825879   2.023528  ...   0.186695  -0.412164  -1.492652   
2331 -1.865555 -0.350308  -0.649167  ...   0.415677  -0.011177  -0.116519   
2332 -0.193449 -0.264206  -0.775251  ...  -0.481061   0.170483  -0.782933   
2333  0.318000 -1.748022  -0.254789  ...   0.186323   0.170921  -0.141426   
2334 -1.402850 -0.757913  -0.143048  ...   1.883027   0.426062  -0.134889   

      sensor_27  sensor_28  sensor_29  sensor_30  sensor_31  sensor_32  target  
0      0.271689   1.408115  -0.263322  -0.702508  -0.238269  -0.735616       1  
1      0.338467   0.704214   0.847177  -0.129756  -0.155609  -0.974972       1  
2      0.468867   0.392232  -3.454223  -0.529888  -0.319460  -0.316562       0  
3      0.387015  -0.065044  -0.336256  -0.398988  -0.513363  -0.184111       1  
4     -0.501660   1.104734   0.180913   0.531208   0.469003  -1.661853       2  
...         ...        ...        ...        ...        ...        ...     ...  
2330  -1.460590   1.999079  -0.352083  -1.753098  -0.203639   0.491784       3  
2331   0.921653  -0.770691   0.170515   0.119370   1.139607  -0.053905       3  
2332  -1.465457   0.966048   0.099710  -1.490799  -0.278190  -0.057058       3  
2333  -0.232203  -0.455245  -0.500671  -0.534043   0.589805  -0.741910       1  
2334  -2.274164  -1.421664  -0.077221   0.155940  -0.868996  -0.801226       2  

[2335 rows x 33 columns]

In [6]:
train_x=train.drop('target',axis=1)
train_y=train['target']

In [17]:
from catboost import CatBoostClassifier

In [9]:
CatBoostClassifier(verbose=True,n_estimators=100)

In [20]:
#GridSearchCV 를 이용해 모델들을 최적화시켜줍니다.
from tqdm.auto import tqdm


classifier = CatBoostClassifier(verbose=True,task_type="GPU")

params = {
        'n_estimators':[50,100,150,1000],
        'learning_rate': [0.03, 0.1],
        'depth': [4, 6, 10],
        'l2_leaf_reg': [1, 3, 5, 7, 9]
}


grid_result = classifier.grid_search(params,
                      X=train_x,
                      y=train_y,
                      plot=True
                      )


Custom logger is already specified. Specify more than one logger at same time is not thread safe.

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 1.3740165	test: 1.3750494	best: 1.3750494 (0)	total: 10.3ms	remaining: 507ms
1:	learn: 1.3625304	test: 1.3650398	best: 1.3650398 (1)	total: 17.8ms	remaining: 427ms
2:	learn: 1.3505316	test: 1.3544817	best: 1.3544817 (2)	total: 23ms	remaining: 360ms
3:	learn: 1.3393949	test: 1.3448808	best: 1.3448808 (3)	total: 29.2ms	remaining: 336ms
4:	learn: 1.3282839	test: 1.3350549	best: 1.3350549 (4)	total: 34.4ms	remaining: 310ms
5:	learn: 1.3176988	test: 1.3253021	best: 1.3253021 (5)	total: 40.2ms	remaining: 295ms
6:	learn: 1.3074082	test: 1.3165069	best: 1.3165069 (6)	total: 46.4ms	remaining: 285ms
7:	learn: 1.2982044	test: 1.3086735	best: 1.3086735 (7)	total: 51.7ms	remaining: 271ms
8:	learn: 1.2895940	test: 1.3018344	best: 1.3018344 (8)	total: 57.1ms	remaining: 260ms
9:	learn: 1.2809571	test: 1.2926993	best: 1.2926993 (9)	total: 63.6ms	remaining: 254ms
10:	learn: 1.2720278	test: 1.2857173	best: 1.2857173 (10)	total: 69.3ms	remaining: 246ms
11:	learn: 1.2632710	test: 1.2785043	best: 

4:	learn: 1.3323640	test: 1.3385943	best: 1.3385943 (4)	total: 33ms	remaining: 297ms
5:	learn: 1.3225505	test: 1.3294542	best: 1.3294542 (5)	total: 39ms	remaining: 286ms
6:	learn: 1.3128415	test: 1.3211705	best: 1.3211705 (6)	total: 44.8ms	remaining: 275ms
7:	learn: 1.3041696	test: 1.3138159	best: 1.3138159 (7)	total: 52.9ms	remaining: 278ms
8:	learn: 1.2960389	test: 1.3073558	best: 1.3073558 (8)	total: 60.9ms	remaining: 277ms
9:	learn: 1.2878192	test: 1.2986259	best: 1.2986259 (9)	total: 68.6ms	remaining: 274ms
10:	learn: 1.2793011	test: 1.2918936	best: 1.2918936 (10)	total: 75.8ms	remaining: 269ms
11:	learn: 1.2714771	test: 1.2847101	best: 1.2847101 (11)	total: 81.6ms	remaining: 259ms
12:	learn: 1.2636864	test: 1.2782944	best: 1.2782944 (12)	total: 88ms	remaining: 250ms
13:	learn: 1.2562155	test: 1.2719583	best: 1.2719583 (13)	total: 93.5ms	remaining: 240ms
14:	learn: 1.2490223	test: 1.2656577	best: 1.2656577 (14)	total: 99.3ms	remaining: 232ms
15:	learn: 1.2417440	test: 1.2591188	be

1:	learn: 1.3657545	test: 1.3678399	best: 1.3678399 (1)	total: 13.9ms	remaining: 332ms
2:	learn: 1.3549803	test: 1.3581698	best: 1.3581698 (2)	total: 19.2ms	remaining: 301ms
3:	learn: 1.3452980	test: 1.3497603	best: 1.3497603 (3)	total: 24.7ms	remaining: 284ms
4:	learn: 1.3352333	test: 1.3409254	best: 1.3409254 (4)	total: 30.4ms	remaining: 274ms
5:	learn: 1.3259790	test: 1.3322665	best: 1.3322665 (5)	total: 36.8ms	remaining: 270ms
6:	learn: 1.3167246	test: 1.3243807	best: 1.3243807 (6)	total: 42.4ms	remaining: 260ms
7:	learn: 1.3087367	test: 1.3172930	best: 1.3172930 (7)	total: 48.2ms	remaining: 253ms
8:	learn: 1.3010037	test: 1.3111503	best: 1.3111503 (8)	total: 54.1ms	remaining: 246ms
9:	learn: 1.2931192	test: 1.3027603	best: 1.3027603 (9)	total: 59.5ms	remaining: 238ms
10:	learn: 1.2849505	test: 1.2962636	best: 1.2962636 (10)	total: 65.3ms	remaining: 231ms
11:	learn: 1.2769968	test: 1.2896385	best: 1.2896385 (11)	total: 71.4ms	remaining: 226ms
12:	learn: 1.2699452	test: 1.2837540	be

...

557:	learn: 0.0616734	test: 0.4460687	best: 0.4460687 (557)	total: 5.29s	remaining: 4.19s
558:	learn: 0.0614334	test: 0.4461076	best: 0.4460687 (557)	total: 5.29s	remaining: 4.18s
559:	learn: 0.0612483	test: 0.4464696	best: 0.4460687 (557)	total: 5.3s	remaining: 4.17s
560:	learn: 0.0610287	test: 0.4460817	best: 0.4460687 (557)	total: 5.32s	remaining: 4.16s
561:	learn: 0.0607917	test: 0.4460697	best: 0.4460687 (557)	total: 5.32s	remaining: 4.15s
562:	learn: 0.0605106	test: 0.4457692	best: 0.4457692 (562)	total: 5.33s	remaining: 4.14s
563:	learn: 0.0603939	test: 0.4457057	best: 0.4457057 (563)	total: 5.34s	remaining: 4.13s
564:	learn: 0.0601373	test: 0.4452927	best: 0.4452927 (564)	total: 5.35s	remaining: 4.12s
565:	learn: 0.0599117	test: 0.4453630	best: 0.4452927 (564)	total: 5.36s	remaining: 4.11s
566:	learn: 0.0597873	test: 0.4453419	best: 0.4452927 (564)	total: 5.37s	remaining: 4.1s
567:	learn: 0.0596444	test: 0.4451223	best: 0.4451223 (567)	total: 5.38s	remaining: 4.09s
568:	learn: 

657:	learn: 0.0476856	test: 0.4393642	best: 0.4393617 (656)	total: 6.26s	remaining: 3.25s
658:	learn: 0.0475315	test: 0.4391552	best: 0.4391552 (658)	total: 6.27s	remaining: 3.24s
659:	learn: 0.0474499	test: 0.4390320	best: 0.4390320 (659)	total: 6.28s	remaining: 3.23s
660:	learn: 0.0473740	test: 0.4390328	best: 0.4390320 (659)	total: 6.29s	remaining: 3.22s
661:	learn: 0.0472650	test: 0.4388954	best: 0.4388954 (661)	total: 6.3s	remaining: 3.21s
662:	learn: 0.0471315	test: 0.4387544	best: 0.4387544 (662)	total: 6.31s	remaining: 3.21s
663:	learn: 0.0470351	test: 0.4387853	best: 0.4387544 (662)	total: 6.32s	remaining: 3.2s
664:	learn: 0.0469311	test: 0.4388007	best: 0.4387544 (662)	total: 6.33s	remaining: 3.19s
665:	learn: 0.0468329	test: 0.4386946	best: 0.4386946 (665)	total: 6.34s	remaining: 3.18s
666:	learn: 0.0467402	test: 0.4386607	best: 0.4386607 (666)	total: 6.35s	remaining: 3.17s
667:	learn: 0.0466560	test: 0.4387492	best: 0.4386607 (666)	total: 6.36s	remaining: 3.16s
668:	learn: 

757:	learn: 0.0385150	test: 0.4352277	best: 0.4351241 (744)	total: 7.22s	remaining: 2.31s
758:	learn: 0.0384412	test: 0.4351277	best: 0.4351241 (744)	total: 7.23s	remaining: 2.3s
759:	learn: 0.0383338	test: 0.4350981	best: 0.4350981 (759)	total: 7.24s	remaining: 2.29s
760:	learn: 0.0382561	test: 0.4350361	best: 0.4350361 (760)	total: 7.25s	remaining: 2.28s
761:	learn: 0.0381785	test: 0.4347902	best: 0.4347902 (761)	total: 7.26s	remaining: 2.27s
762:	learn: 0.0381058	test: 0.4346907	best: 0.4346907 (762)	total: 7.27s	remaining: 2.26s
763:	learn: 0.0380010	test: 0.4348270	best: 0.4346907 (762)	total: 7.28s	remaining: 2.25s
764:	learn: 0.0379353	test: 0.4347253	best: 0.4346907 (762)	total: 7.29s	remaining: 2.24s
765:	learn: 0.0378597	test: 0.4344634	best: 0.4344634 (765)	total: 7.3s	remaining: 2.23s
766:	learn: 0.0377246	test: 0.4342317	best: 0.4342317 (766)	total: 7.31s	remaining: 2.22s
767:	learn: 0.0376452	test: 0.4342696	best: 0.4342317 (766)	total: 7.32s	remaining: 2.21s
768:	learn: 

855:	learn: 0.0318163	test: 0.4300662	best: 0.4295863 (844)	total: 8.18s	remaining: 1.38s
856:	learn: 0.0317437	test: 0.4299149	best: 0.4295863 (844)	total: 8.19s	remaining: 1.37s
857:	learn: 0.0316730	test: 0.4298609	best: 0.4295863 (844)	total: 8.2s	remaining: 1.36s
858:	learn: 0.0316179	test: 0.4298633	best: 0.4295863 (844)	total: 8.21s	remaining: 1.35s
859:	learn: 0.0315732	test: 0.4297874	best: 0.4295863 (844)	total: 8.22s	remaining: 1.34s
860:	learn: 0.0314858	test: 0.4295385	best: 0.4295385 (860)	total: 8.23s	remaining: 1.33s
861:	learn: 0.0314229	test: 0.4295116	best: 0.4295116 (861)	total: 8.24s	remaining: 1.32s
862:	learn: 0.0313934	test: 0.4294199	best: 0.4294199 (862)	total: 8.25s	remaining: 1.31s
863:	learn: 0.0313147	test: 0.4293814	best: 0.4293814 (863)	total: 8.26s	remaining: 1.3s
864:	learn: 0.0312585	test: 0.4292574	best: 0.4292574 (864)	total: 8.27s	remaining: 1.29s
865:	learn: 0.0311958	test: 0.4290501	best: 0.4290501 (865)	total: 8.28s	remaining: 1.28s
866:	learn: 

953:	learn: 0.0268335	test: 0.4276022	best: 0.4275828 (952)	total: 9.14s	remaining: 441ms
954:	learn: 0.0268060	test: 0.4274959	best: 0.4274959 (954)	total: 9.15s	remaining: 431ms
955:	learn: 0.0267580	test: 0.4275277	best: 0.4274959 (954)	total: 9.16s	remaining: 422ms
956:	learn: 0.0267318	test: 0.4274579	best: 0.4274579 (956)	total: 9.17s	remaining: 412ms
957:	learn: 0.0267138	test: 0.4273914	best: 0.4273914 (957)	total: 9.18s	remaining: 402ms
958:	learn: 0.0266707	test: 0.4273343	best: 0.4273343 (958)	total: 9.19s	remaining: 393ms
959:	learn: 0.0266302	test: 0.4272723	best: 0.4272723 (959)	total: 9.2s	remaining: 383ms
960:	learn: 0.0266052	test: 0.4272886	best: 0.4272723 (959)	total: 9.21s	remaining: 374ms
961:	learn: 0.0265587	test: 0.4274036	best: 0.4272723 (959)	total: 9.22s	remaining: 364ms
962:	learn: 0.0265252	test: 0.4274575	best: 0.4272723 (959)	total: 9.23s	remaining: 355ms
963:	learn: 0.0264847	test: 0.4273279	best: 0.4272723 (959)	total: 9.24s	remaining: 345ms
964:	learn:

In [23]:
grid_result

{'params': {'depth': 6,
  'l2_leaf_reg': 3,
  'iterations': 1000,
  'learning_rate': 0.1},
 'cv_results': defaultdict(list,
             {'iterations': [0,
               1,
               2,
               3,
               4,
               5,
               6,
               7,
               8,
               9,
               10,
               11,
               12,
               13,
               14,
               15,
               16,
               17,
               18,
               19,
               20,
               21,
               22,
               23,
               24,
               25,
               26,
               27,
               28,
               29,
               30,
               31,
               32,
               33,
               34,
               35,
               36,
               37,
               38,
               39,
               40,
               41,
               42,
               43,
               44,
               45

In [22]:
classifier = CatBoostClassifier(depth=6,l2_leaf_reg=3,learning_rate=0.1,iterations=1000,verbose=True,task_type="GPU")

In [30]:
classifier.get_test_eval()

CatBoostError: The model has been trained without an eval set.

In [24]:
classifier.fit(train_x, train_y)
y_pred = classifier.predict(test.drop('id',axis=1))

0:	learn: 1.3421587	total: 16.9ms	remaining: 16.8s
1:	learn: 1.3032028	total: 26.5ms	remaining: 13.2s
2:	learn: 1.2680096	total: 35.5ms	remaining: 11.8s
3:	learn: 1.2362546	total: 43.9ms	remaining: 10.9s
4:	learn: 1.2079808	total: 52.7ms	remaining: 10.5s
5:	learn: 1.1818562	total: 62.9ms	remaining: 10.4s
6:	learn: 1.1566728	total: 71.3ms	remaining: 10.1s
7:	learn: 1.1326034	total: 80.1ms	remaining: 9.93s
8:	learn: 1.1099624	total: 90.4ms	remaining: 9.96s
9:	learn: 1.0911317	total: 99.1ms	remaining: 9.81s
10:	learn: 1.0723843	total: 109ms	remaining: 9.81s
11:	learn: 1.0554539	total: 118ms	remaining: 9.71s
12:	learn: 1.0381415	total: 127ms	remaining: 9.65s
13:	learn: 1.0212090	total: 137ms	remaining: 9.67s
14:	learn: 1.0055638	total: 146ms	remaining: 9.62s
15:	learn: 0.9920585	total: 156ms	remaining: 9.57s
16:	learn: 0.9760667	total: 165ms	remaining: 9.54s
17:	learn: 0.9633251	total: 174ms	remaining: 9.51s
18:	learn: 0.9502004	total: 183ms	remaining: 9.46s
19:	learn: 0.9358069	total: 192

166:	learn: 0.3060007	total: 1.56s	remaining: 7.77s
167:	learn: 0.3041070	total: 1.57s	remaining: 7.76s
168:	learn: 0.3029029	total: 1.58s	remaining: 7.76s
169:	learn: 0.3019598	total: 1.58s	remaining: 7.74s
170:	learn: 0.3001336	total: 1.59s	remaining: 7.73s
171:	learn: 0.2987016	total: 1.6s	remaining: 7.72s
172:	learn: 0.2965565	total: 1.61s	remaining: 7.72s
173:	learn: 0.2952844	total: 1.63s	remaining: 7.72s
174:	learn: 0.2942734	total: 1.63s	remaining: 7.71s
175:	learn: 0.2928597	total: 1.64s	remaining: 7.7s
176:	learn: 0.2909485	total: 1.65s	remaining: 7.69s
177:	learn: 0.2896889	total: 1.66s	remaining: 7.69s
178:	learn: 0.2882747	total: 1.68s	remaining: 7.68s
179:	learn: 0.2875771	total: 1.68s	remaining: 7.67s
180:	learn: 0.2862947	total: 1.69s	remaining: 7.67s
181:	learn: 0.2851347	total: 1.7s	remaining: 7.66s
182:	learn: 0.2835618	total: 1.71s	remaining: 7.65s
183:	learn: 0.2822532	total: 1.72s	remaining: 7.64s
184:	learn: 0.2811598	total: 1.73s	remaining: 7.63s
185:	learn: 0.2

328:	learn: 0.1506707	total: 3.06s	remaining: 6.25s
329:	learn: 0.1502056	total: 3.07s	remaining: 6.24s
330:	learn: 0.1496893	total: 3.08s	remaining: 6.23s
331:	learn: 0.1492483	total: 3.09s	remaining: 6.22s
332:	learn: 0.1488080	total: 3.1s	remaining: 6.21s
333:	learn: 0.1482475	total: 3.11s	remaining: 6.2s
334:	learn: 0.1476665	total: 3.12s	remaining: 6.19s
335:	learn: 0.1473188	total: 3.13s	remaining: 6.18s
336:	learn: 0.1467446	total: 3.14s	remaining: 6.17s
337:	learn: 0.1460325	total: 3.15s	remaining: 6.17s
338:	learn: 0.1454785	total: 3.16s	remaining: 6.16s
339:	learn: 0.1446149	total: 3.17s	remaining: 6.15s
340:	learn: 0.1442412	total: 3.17s	remaining: 6.14s
341:	learn: 0.1437723	total: 3.19s	remaining: 6.13s
342:	learn: 0.1433901	total: 3.19s	remaining: 6.12s
343:	learn: 0.1427065	total: 3.2s	remaining: 6.11s
344:	learn: 0.1421980	total: 3.21s	remaining: 6.1s
345:	learn: 0.1417420	total: 3.22s	remaining: 6.09s
346:	learn: 0.1412797	total: 3.23s	remaining: 6.08s
347:	learn: 0.14

506:	learn: 0.0855890	total: 4.73s	remaining: 4.6s
507:	learn: 0.0854139	total: 4.74s	remaining: 4.59s
508:	learn: 0.0851739	total: 4.75s	remaining: 4.58s
509:	learn: 0.0848728	total: 4.76s	remaining: 4.57s
510:	learn: 0.0845748	total: 4.77s	remaining: 4.56s
511:	learn: 0.0843902	total: 4.78s	remaining: 4.55s
512:	learn: 0.0841441	total: 4.79s	remaining: 4.55s
513:	learn: 0.0839653	total: 4.8s	remaining: 4.54s
514:	learn: 0.0837473	total: 4.81s	remaining: 4.53s
515:	learn: 0.0834846	total: 4.82s	remaining: 4.52s
516:	learn: 0.0833237	total: 4.83s	remaining: 4.51s
517:	learn: 0.0830111	total: 4.84s	remaining: 4.5s
518:	learn: 0.0828118	total: 4.85s	remaining: 4.49s
519:	learn: 0.0825931	total: 4.86s	remaining: 4.48s
520:	learn: 0.0824060	total: 4.87s	remaining: 4.47s
521:	learn: 0.0822553	total: 4.88s	remaining: 4.47s
522:	learn: 0.0820805	total: 4.89s	remaining: 4.46s
523:	learn: 0.0818693	total: 4.9s	remaining: 4.45s
524:	learn: 0.0817369	total: 4.91s	remaining: 4.44s
525:	learn: 0.08

682:	learn: 0.0545517	total: 6.41s	remaining: 2.98s
683:	learn: 0.0544380	total: 6.42s	remaining: 2.97s
684:	learn: 0.0543078	total: 6.43s	remaining: 2.96s
685:	learn: 0.0541517	total: 6.44s	remaining: 2.95s
686:	learn: 0.0539435	total: 6.45s	remaining: 2.94s
687:	learn: 0.0537669	total: 6.46s	remaining: 2.93s
688:	learn: 0.0536440	total: 6.47s	remaining: 2.92s
689:	learn: 0.0535396	total: 6.48s	remaining: 2.91s
690:	learn: 0.0533828	total: 6.49s	remaining: 2.9s
691:	learn: 0.0532450	total: 6.5s	remaining: 2.89s
692:	learn: 0.0531620	total: 6.51s	remaining: 2.88s
693:	learn: 0.0530518	total: 6.52s	remaining: 2.87s
694:	learn: 0.0529497	total: 6.53s	remaining: 2.87s
695:	learn: 0.0528162	total: 6.54s	remaining: 2.85s
696:	learn: 0.0526439	total: 6.55s	remaining: 2.85s
697:	learn: 0.0525453	total: 6.56s	remaining: 2.84s
698:	learn: 0.0524734	total: 6.57s	remaining: 2.83s
699:	learn: 0.0523774	total: 6.58s	remaining: 2.82s
700:	learn: 0.0522908	total: 6.58s	remaining: 2.81s
701:	learn: 0.

857:	learn: 0.0375574	total: 8.14s	remaining: 1.35s
858:	learn: 0.0374794	total: 8.15s	remaining: 1.34s
859:	learn: 0.0374054	total: 8.16s	remaining: 1.33s
860:	learn: 0.0373181	total: 8.17s	remaining: 1.32s
861:	learn: 0.0372460	total: 8.18s	remaining: 1.31s
862:	learn: 0.0371960	total: 8.19s	remaining: 1.3s
863:	learn: 0.0371473	total: 8.2s	remaining: 1.29s
864:	learn: 0.0370929	total: 8.21s	remaining: 1.28s
865:	learn: 0.0370458	total: 8.22s	remaining: 1.27s
866:	learn: 0.0369975	total: 8.23s	remaining: 1.26s
867:	learn: 0.0369338	total: 8.24s	remaining: 1.25s
868:	learn: 0.0368658	total: 8.25s	remaining: 1.24s
869:	learn: 0.0368128	total: 8.26s	remaining: 1.23s
870:	learn: 0.0367449	total: 8.27s	remaining: 1.22s
871:	learn: 0.0366908	total: 8.28s	remaining: 1.21s
872:	learn: 0.0365976	total: 8.29s	remaining: 1.21s
873:	learn: 0.0365098	total: 8.29s	remaining: 1.2s
874:	learn: 0.0364514	total: 8.3s	remaining: 1.19s
875:	learn: 0.0364021	total: 8.31s	remaining: 1.18s
876:	learn: 0.03

In [25]:
y_pred

array([[0],
       [0],
       [1],
       ...,
       [0],
       [0],
       [3]], dtype=int64)

In [26]:
submission = pd.read_csv('./data/sample_submission.csv')
submission.head()

id  target
0   1       0
1   2       0
2   3       0
3   4       0
4   5       0

In [27]:
submission['target']=y_pred
submission

id  target
0        1       0
1        2       0
2        3       1
3        4       3
4        5       2
...    ...     ...
9338  9339       3
9339  9340       1
9340  9341       0
9341  9342       0
9342  9343       3

[9343 rows x 2 columns]

In [28]:
submission.to_csv('./submit.csv',index=False)